In [1]:
!pip install transformers
!pip install fasttext

Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 21.1 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 5.0 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 38.8 MB/s eta 0:00:00:00:0100:01
Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 68.8/68.8 kB 4.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for fasttext: filename=fasttext-0.9.2-cp310-cp310-linux_x86_64.whl size=286957 sha256=ec652aaf90beb63b6929b47c4dd18d2771b41166fa2a5b61cd3de4a0aa9addd6
  Stored in directory: /home/ec2-user/.cache/pip/wheels/fc/22/93/1a3d535655339964fd8936d807ec85da466303d545023d2139
Successfully built fasttext


In [2]:
import pandas as pd
import json 
import os
import warnings
warnings.filterwarnings("ignore")
import pyarrow as pa
import pyarrow.parquet as pq
import tensorflow as tf 
import re
from datetime import datetime
from tqdm import tqdm, tqdm_notebook
tqdm_notebook().pandas()
import fasttext

0it [00:00, ?it/s]

In [3]:
# load the pre-trained models: 
from transformers import RobertaTokenizer, TFRobertaModel
with tf.device('/device:GPU:0'):
    tokenizer = RobertaTokenizer.from_pretrained("roberta-base")
    model = TFRobertaModel.from_pretrained("roberta-base")

Some layers from the model checkpoint at roberta-base were not used when initializing TFRobertaModel: ['lm_head']
- This IS expected if you are initializing TFRobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFRobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFRobertaModel were initialized from the model checkpoint at roberta-base.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFRobertaModel for predictions without further training.


In [4]:
def prepare_data(input_text, tokenizer):
    with tf.device('/device:GPU:0'):
#         gc.collect()
        token = tokenizer.encode_plus(
            input_text,
            max_length=256, 
            truncation=True, 
            padding='max_length', 
            add_special_tokens=True,
            return_tensors='tf'
        )
        return {
            'input_ids': tf.cast(token.input_ids, tf.float64),
            'attention_mask': tf.cast(token.attention_mask, tf.float64)
        }

def make_predictions(model, input_text,threshold, label_list=None ): 
    with tf.device('/device:GPU:0'):
#         gc.collect()
        processed_data = prepare_data(input_text, tokenizer)
        probs = model.predict(processed_data)
#         print(probs)
        if probs[0]> threshold: 
            return label_list[0]
        else: 
            return label_list[1]
#     return(probs[0])

In [5]:
# zero_star_model = tf.keras.models.load_model('zero_star_general_fnl')
rating_management_explicit= tf.keras.models.load_model('/home/ec2-user/SageMaker/3000k_augmented_rating_management_explicit_model_1')

In [6]:
# path to predicted results: 
path = '/home/ec2-user/SageMaker/predicted_resultsa'
os.listdir(path)

['amazon_reviews_office_2.json.json_predicted.json',
 'amazon_reviews_office_4.json.json_predicted.json',
 'Untitled.ipynb',
 'amazon_reviews_office_6.json.json_predicted.json',
 'amazon_reviews_office_8.json.json_predicted.json',
 '.ipynb_checkpoints',
 'amazon_reviews_office_0.json.json_predicted.json']

In [ ]:
# rating management explicit
import gc 
gc.collect()
file = 'amazon_reviews_office_8'
# path = os.path.join(os.getcwd(), 'predicted_results')
major_df = pd.read_json(os.path.join(path,'amazon_reviews_office_8.json.json_predicted.json') )
label_list= [1, 0]
major_df['rating_management_explicit']= major_df.review_body.progress_apply(lambda x: make_predictions(rating_management_explicit, x,
                                                                            0.5, label_list))
major_df.to_json(f'{file}_rating_predicted.json')

  0%|          | 0/158515 [00:00<?, ?it/s]

1/1 [==============================] - 0s 42ms/step


1/1 [==============================] - 0s 46ms/step


1/1 [==============================] - 0s 42ms/step


1/1 [==============================] - 0s 45ms/step


...

1/1 [==============================] - 0s 43ms/step


1/1 [==============================] - 0s 43ms/step


1/1 [==============================] - 0s 42ms/step


1/1 [==============================] - 0s 42ms/step


1/1 [==============================] - 0s 42ms/step


In [ ]:
print('done')

In [ ]:
major_df.to_json(f'{file}_rating_predicted.json') 

In [11]:
major_df[major_df.rating_management_explicit==1].review_body.iloc[10]

"Avoid this bulb at all costs.  The positive reviews sound just a little too canned to me, and the negatives hit my experience on the head.  I put the new lamp in, it worked for about 2 minutes, and then the projector shut down.  I figured I'd put the old bulb back in and run that (the old one was still functional, just getting on in hours) and the problem persists.  I don't know if it's possible that a bulb can wreck the projector, but it's suspect that everything was fine before this bulb went in.Save yourself a headache and order direct from BenQ.  It'll cost more, but piece of mind is expensive."

In [12]:
major_df.rating_management_explicit.value_counts()

0    160789
1        25
Name: rating_management_explicit, dtype: int64